In [460]:
# !pip install autogluon==0.5.2

In [461]:
import numpy as np
import pandas as pd
import pathlib
import pandas as pd
from autogluon.timeseries import TimeSeriesDataFrame, TimeSeriesPredictor
import matplotlib.pyplot as plt
from sklearn.preprocessing import StandardScaler

# AutoGluon

AutoGluon can be used to run automatically or with more precise configurations. Included models are listed here:
https://auto.gluon.ai/stable/tutorials/timeseries/forecasting-model-zoo.html

To fit our experiment design, it may make the most sense to run models separately. This way we'll can collect all of the forecasts produced by each model type, rather than ending up with forecasts produced by different methods all being called AutoGluon. That said, if we want to treat AutoGluon as a closed method, we can (any maybe should!) do that as well, if for no other reason to highlight the power of Auto* frameworks.

So to be clear, we can initially experiment with the underlying models' separately, e.g. with:
- NaiveModel
- ...
- TemporalFusionTransformerModel

And at the end, we can consider the use of AutoGluon's presets (e.g. `'fast_training'` and `'best_quality'`) where we would just consider those to be 'techniques' themselves to compare in a special analysis to see whether AutoGluon could have just produced the best forecast on its own.


Higher quality presets usually result in better forecasts but take longer to train. The following presets are available:

- "fast_training": fit simple statistical models (ETS, Theta, Naive, SeasonalNaive) + fast tree-based model RecursiveTabular. These models are fast to train but may not be very accurate.

- "medium_quality": all models mentioned above + deep learning model DeepAR. Default setting that produces good forecasts with reasonable training time.

- "high_quality": all models mentioned above + automatically tuned statistical models (AutoETS, AutoARIMA) + tree-based model DirectTabular + deep learning models TemporalFusionTransformer and PatchTST . Much more accurate than medium_quality, but takes longer to train.

- "best_quality": all models mentioned above + more tabular models + training multiple copies of DeepAR. Usually better than high_quality, but takes even longer to train.


In [462]:
AVAILABLE_PRESETS = [
    "fast_training",
    "medium_quality",
    "high_quality",
    "best_quality"
]

In [463]:
# # EXP_BASE = "autogluon_global_with_scaled_covariates_experiment_preset"
# # EXP_BASE = "autogluon_global_mean_SWE__covariates_preset"
# # EXP_BASE = "autogluon_global_with_scaled_covariates_experiment_preset"
# # EXP_BASE = "autogluon_preset_best_quality_global_model"
# # EXP_BASE = "autogluon_preset_best_quality_model"


# # EXP_BASE = "autogluon_with_scaled_covariates_Energy_EXCAUS"
# EXP_BASE = "autogluon_global_with_scaled_covariates_experiment"


# # Run all of these:
# # EXP_BASE = "autogluon_global_with_scaled_covariates"
# # EXP_BASE = "autogluon_global_with_scaled_covariates_climate_vars"
# # EXP_BASE = "autogluon_with_covariates"
# # EXP_BASE = "autogluon_global_with_scaled_covariates"
# # EXP_BASE = "autogluon_global_with_covariates"
# # EXP_MODEL_LIST = ["NaiveModel"]
# # EXP_MODEL_LIST = ["NaiveModel", "SeasonalNaiveModel", "ARIMAModel", "ETSModel", "AutoETSModel"]
# # EXP_MODEL_LIST = ["DLinearModel"]
# # EXP_MODEL_LIST = ["DeepARModel"]
# # EXP_MODEL_LIST = ["DirectTabularModel", "RecursiveTabularModel", "PatchTSTModel", "SimpleFeedForwardModel", "TemporalFusionTransformerModel"]
# # EXP_MODEL_LIST = ["PatchTSTModel", "SimpleFeedForwardModel", "TemporalFusionTransformerModel"]

# # EXP_MODEL_LIST = ["TemporalFusionTransformerModel", "best_quality"]
# EXP_MODEL_LIST = ["TemporalFusionTransformerModel", "DirectTabularModel"]
# # EXP_MODEL_LIST = ["best_quality"]
# # EXP_MODEL_LIST = ["medium_quality"]



## Load data

In [464]:
# df = pd.read_csv("../data/processed_data_inputs/Connex.csv", index_col=0)
df = pd.read_csv("../../data/processed_data_inputs/Connex.csv", index_col=0)

df.index = pd.to_datetime(df.index)
df.head()

# prediction_length = 12
context_length=52
set_freq = 'W'

df = df.resample(set_freq).sum()

In [465]:
#Define target categories 
# target_categories = ['IS_MENTAL_HEALTH', 'IS_SUBSTANCE_ABUSE']
target_categories = ['IS_MENTAL_HEALTH']

target_categories

['IS_MENTAL_HEALTH']

In [466]:
## As a place-holder using parallel CONNEX datasets as covariates 
# all_data = df.drop(columns=target_categories)
main_data = df
main_data.index.name = None


In [467]:
#Collect Government of Ontario COVID-19 datasets 
# covid_data = pd.read_csv("../data/processed_data_inputs/COVID19.csv", index_col=0)
covid_data = pd.read_csv("../../data/processed_data_inputs/COVID19.csv", index_col=0)

covid_data.index = pd.to_datetime(covid_data.index)

#Collect google trends data 
# google_data = pd.read_csv("../data/processed_data_inputs/GoogleTrends.csv", index_col=0)
google_data = pd.read_csv("../../data/processed_data_inputs/GoogleTrends.csv", index_col=0)

google_data.index = pd.to_datetime(google_data.index)


#Collect Statistics Canada data
# statcan_data = pd.read_csv("../data/processed_data_inputs/StatCan.csv", index_col=0)
statcan_data = pd.read_csv("../../data/processed_data_inputs/StatCan.csv", index_col=0)
statcan_data.index = pd.to_datetime(statcan_data.index)
statcan_data = statcan_data.resample(set_freq).interpolate(method='linear')


#Combine the three sources of covariates
all_covs = google_data.join(covid_data, how='left')

all_covs = all_covs.join(statcan_data, how='left')


# Check for duplicate indices
duplicate_indices = all_covs.index.duplicated(keep='first')
# print("Duplicate Indices:")
# print(all_covs[duplicate_indices])

# Drop duplicate indices
all_covs = all_covs[~duplicate_indices]
all_covs

google_anxiety  google_suicide  google_fear  google_loneliness  \
2018-01-07            82.0            33.0         38.0               48.0   
2018-01-14            84.0            32.0         38.0              100.0   
2018-01-21            87.0            26.0         35.0               70.0   
2018-01-28            92.0            27.0         35.0               43.0   
2018-02-04            80.0            23.0         35.0               47.0   
...                    ...             ...          ...                ...   
2023-01-29            81.0            18.0         42.0               47.0   
2023-02-05            79.0            17.0         41.0               25.0   
2023-02-12            78.0            16.0         39.0               56.0   
2023-02-19            82.0            19.0         37.0               40.0   
2023-02-26            88.0            17.0         35.0               41.0   

            google_allmentaldistress  google_mortgage  google_mortgageloan  \
2018-01-07                     281.0             41.0                 56.0   
2018-01-14                     354.0             48.0                 70.0   
2018-01-21                     312.0             40.0                 43.0   
2018-01-28                     294.0             37.0                 44.0   
2018-02-04                     273.0             34.0                 76.0   
...                              ...              ...                  ...   
2023-01-29                     263.0             48.0                 74.0   
2023-02-05                     227.0             42.0                 55.0   
2023-02-12                     254.0             38.0                 70.0   
2023-02-19                     239.0             42.0                 85.0   
2023-02-26                     247.0             44.0                 51.0   

            google_unemployment  google_foodbank  google_welfare  ...  \
2018-01-07                 15.0             20.0            59.0  ...   
2018-01-14                 14.0             21.0            62.0  ...   
2018-01-21                 15.0             18.0            80.0  ...   
2018-01-28                 14.0             23.0            93.0  ...   
2018-02-04                 14.0             11.0            69.0  ...   
...                         ...              ...             ...  ...   
2023-01-29                 13.0             50.0            65.0  ...   
2023-02-05                 12.0             21.0            66.0  ...   
2023-02-12                 10.0             48.0            47.0  ...   
2023-02-19                  8.0             35.0            52.0  ...   
2023-02-26                  8.0             34.0            57.0  ...   

            statcan_Energy  statcan_Food  statcan_Gasoline  statcan_Goods  \
2018-01-07      161.969231    144.692308        181.738462     118.923077   
2018-01-14      162.488462    144.884615        182.776923     119.046154   
2018-01-21      163.007692    145.076923        183.815385     119.169231   
2018-01-28      163.526923    145.269231        184.853846     119.292308   
2018-02-04      164.046154    145.461538        185.892308     119.415385   
...                    ...           ...               ...            ...   
2023-01-29      203.800000    183.500000        216.600000     139.500000   
2023-02-05      203.800000    183.500000        216.600000     139.500000   
2023-02-12      203.800000    183.500000        216.600000     139.500000   
2023-02-19      203.800000    183.500000        216.600000     139.500000   
2023-02-26      203.800000    183.500000        216.600000     139.500000   

            statcan_Health and personal care  \
2018-01-07                        127.769231   
2018-01-14                        127.838462   
2018-01-21                        127.907692   
2018-01-28                        127.976923   
2018-02-04                        128.046154   
...                                      ...   


In [468]:
main_data = main_data.asfreq(set_freq)
all_covs = all_covs.asfreq(set_freq)

all_data = main_data.join(all_covs, how='left')
# all_data = all_data.dropna()

# all_data = main_data



In [469]:
## pre process data 
def interpolate_nans(df):
    """
    Interpolates NaN values linearly column by column in the given DataFrame.

    Parameters:
    df (DataFrame): The input DataFrame with potential NaN values.

    Returns:
    DataFrame: A DataFrame with NaN values linearly interpolated.
    """
    # Iterate over all columns
    for column in df.columns:
        # Check if column contains NaNs
        if df[column].isna().any():
            # Interpolate NaNs linearly
            df[column] = df[column].interpolate(method='linear')
    
    # Return the modified DataFrame
    return df

In [470]:
if "covariates" in EXP_BASE: 
    covariates = all_data

if "12mo_log_change" in EXP_BASE:
    all_data_pct_change = np.log(all_data / all_data.shift(12))
    all_data_pct_change = all_data_pct_change.rename(lambda x: f"{x}_12mo_log_change", axis=1)
    covariates = all_data_pct_change

if "scaled_covariates" in EXP_BASE:
    covariate_columns = all_data.columns[len(target_categories):]
    covariates = all_data[covariate_columns]
    scaler = StandardScaler()
    scaler.fit(covariates)
    covariates = pd.DataFrame(scaler.transform(covariates), index=all_data.index, columns=covariate_columns)

if "climate_vars" in EXP_BASE:
    covariates = covariates[climate_vars.columns]

# if "covariates" in EXP_BASE:
#     all_data = pd.concat([df, covariates], axis=1).dropna()

all_data

IS_MENTAL_HEALTH  IS_SUBSTANCE_ABUSE  IS_PROBLEM_GAMBLING  \
2015-01-04               265                 194                   36   
2015-01-11               601                 523                   78   
2015-01-18               631                 495                   80   
2015-01-25               582                 519                   68   
2015-02-01               641                 526                   81   
...                      ...                 ...                  ...   
2023-05-07              2454                1208                  318   
2023-05-14              1569                1076                  286   
2023-05-21              3286                2207                  709   
2023-05-28              2127                1259                  237   
2023-06-04               882                 466                  121   

            IS_OTHER  connex_IS_MENTAL_HEALTH_Concurrent Disorder Clients  \
2015-01-04         0                                                0.0     
2015-01-11         1                                                0.0     
2015-01-18         3                                                0.0     
2015-01-25         2                                                2.0     
2015-02-01         3                                                3.0     
...              ...                                                ...     
2023-05-07        12                                                0.0     
2023-05-14        13                                                0.0     
2023-05-21        21                                                0.0     
2023-05-28        17                                                0.0     
2023-06-04         4                                                0.0     

            connex_IS_SUBSTANCE_ABUSE_Concurrent Disorder Clients  \
2015-01-04                                                2.0       
2015-01-11                                                0.0       
2015-01-18                                                0.0       
2015-01-25                                                2.0       
2015-02-01                                                5.0       
...                                                       ...       
2023-05-07                                                0.0       
2023-05-14                                                0.0       
2023-05-21                                                0.0       
2023-05-28                                                0.0       
2023-06-04                                                0.0       

            connex_IS_PROBLEM_GAMBLING_Concurrent Disorder Clients  \
2015-01-04                                                0.0        
2015-01-11                                                0.0        
2015-01-18                                                0.0        
2015-01-25                                                2.0        
2015-02-01                                                0.0        
...                                                       ...        
2023-05-07                                                0.0        
2023-05-14                                                0.0        
2023-05-21                                                0.0        
2023-05-28                                                0.0        
2023-06-04                                                0.0        

            connex_IS_OTHER_Concurrent Disorder Clients  \
2015-01-04                                          0.0   
2015-01-11                                          0.0   
2015-01-18                                          0.0   
2015-01-25                                          0.0   
2015-02-01                                          0.0   
...                                                 ...   
2023-05-07                                          0.0   
2023-05-14                                          0.0   
2023-05-2

In [471]:
# Ensure the dataframe only contains the dates necessary 
all_data = all_data.loc[all_data.index >= '2018-01-01']
all_data = all_data.fillna(0)
all_data = all_data.asfreq(set_freq)
all_data

IS_MENTAL_HEALTH  IS_SUBSTANCE_ABUSE  IS_PROBLEM_GAMBLING  \
2018-01-07              1367                 701                  111   
2018-01-14              1486                 832                  170   
2018-01-21              1637                 911                  206   
2018-01-28              1740                 888                  164   
2018-02-04              1739                 892                  171   
...                      ...                 ...                  ...   
2023-05-07              2454                1208                  318   
2023-05-14              1569                1076                  286   
2023-05-21              3286                2207                  709   
2023-05-28              2127                1259                  237   
2023-06-04               882                 466                  121   

            IS_OTHER  connex_IS_MENTAL_HEALTH_Concurrent Disorder Clients  \
2018-01-07       243                                               69.0     
2018-01-14       218                                               84.0     
2018-01-21       206                                               46.0     
2018-01-28       158                                               86.0     
2018-02-04       144                                               87.0     
...              ...                                                ...     
2023-05-07        12                                                0.0     
2023-05-14        13                                                0.0     
2023-05-21        21                                                0.0     
2023-05-28        17                                                0.0     
2023-06-04         4                                                0.0     

            connex_IS_SUBSTANCE_ABUSE_Concurrent Disorder Clients  \
2018-01-07                                               69.0       
2018-01-14                                               94.0       
2018-01-21                                               47.0       
2018-01-28                                               89.0       
2018-02-04                                               87.0       
...                                                       ...       
2023-05-07                                                0.0       
2023-05-14                                                0.0       
2023-05-21                                                0.0       
2023-05-28                                                0.0       
2023-06-04                                                0.0       

            connex_IS_PROBLEM_GAMBLING_Concurrent Disorder Clients  \
2018-01-07                                                7.0        
2018-01-14                                                6.0        
2018-01-21                                                4.0        
2018-01-28                                                1.0        
2018-02-04                                               19.0        
...                                                       ...        
2023-05-07                                                0.0        
2023-05-14                                                0.0        
2023-05-21                                                0.0        
2023-05-28                                                0.0        
2023-06-04                                                0.0        

            connex_IS_OTHER_Concurrent Disorder Clients  \
2018-01-07                                          0.0   
2018-01-14                                          0.0   
2018-01-21                                          0.0   
2018-01-28                                          0.0   
2018-02-04                                          0.0   
...                                                 ...   
2023-05-07                                          0.0   
2023-05-14                                          0.0   
2023-05-2

In [472]:
# Check for duplicate indices
duplicate_indices = df.index.duplicated(keep='first')
print("Duplicate Indices:")
print(df[duplicate_indices])

Duplicate Indices:
Empty DataFrame
Columns: [IS_MENTAL_HEALTH, IS_SUBSTANCE_ABUSE, IS_PROBLEM_GAMBLING, IS_OTHER, connex_IS_MENTAL_HEALTH_Concurrent Disorder Clients, connex_IS_SUBSTANCE_ABUSE_Concurrent Disorder Clients, connex_IS_PROBLEM_GAMBLING_Concurrent Disorder Clients, connex_IS_OTHER_Concurrent Disorder Clients, connex_IS_MENTAL_HEALTH_Concurrent Disorders, connex_IS_SUBSTANCE_ABUSE_Concurrent Disorders, connex_IS_PROBLEM_GAMBLING_Concurrent Disorders, connex_IS_OTHER_Concurrent Disorders, connex_IS_MENTAL_HEALTH_Families, connex_IS_SUBSTANCE_ABUSE_Families, connex_IS_PROBLEM_GAMBLING_Families, connex_IS_OTHER_Families, connex_IS_MENTAL_HEALTH_Clients with Legal Issues, connex_IS_SUBSTANCE_ABUSE_Clients with Legal Issues, connex_IS_PROBLEM_GAMBLING_Clients with Legal Issues, connex_IS_OTHER_Clients with Legal Issues, connex_IS_MENTAL_HEALTH_LGBTQ+, connex_IS_SUBSTANCE_ABUSE_LGBTQ+, connex_IS_PROBLEM_GAMBLING_LGBTQ+, connex_IS_OTHER_LGBTQ+, connex_IS_MENTAL_HEALTH_Homeless Clie

In [473]:
all_covariates = all_data.columns.to_list()
all_covariates

['IS_MENTAL_HEALTH',
 'IS_SUBSTANCE_ABUSE',
 'IS_PROBLEM_GAMBLING',
 'IS_OTHER',
 'connex_IS_MENTAL_HEALTH_Concurrent Disorder Clients',
 'connex_IS_SUBSTANCE_ABUSE_Concurrent Disorder Clients',
 'connex_IS_PROBLEM_GAMBLING_Concurrent Disorder Clients',
 'connex_IS_OTHER_Concurrent Disorder Clients',
 'connex_IS_MENTAL_HEALTH_Concurrent Disorders',
 'connex_IS_SUBSTANCE_ABUSE_Concurrent Disorders',
 'connex_IS_PROBLEM_GAMBLING_Concurrent Disorders',
 'connex_IS_OTHER_Concurrent Disorders',
 'connex_IS_MENTAL_HEALTH_Families',
 'connex_IS_SUBSTANCE_ABUSE_Families',
 'connex_IS_PROBLEM_GAMBLING_Families',
 'connex_IS_OTHER_Families',
 'connex_IS_MENTAL_HEALTH_Clients with Legal Issues',
 'connex_IS_SUBSTANCE_ABUSE_Clients with Legal Issues',
 'connex_IS_PROBLEM_GAMBLING_Clients with Legal Issues',
 'connex_IS_OTHER_Clients with Legal Issues',
 'connex_IS_MENTAL_HEALTH_LGBTQ+',
 'connex_IS_SUBSTANCE_ABUSE_LGBTQ+',
 'connex_IS_PROBLEM_GAMBLING_LGBTQ+',
 'connex_IS_OTHER_LGBTQ+',
 'connex_I

## Define experiment cutoff dates

Our experiment design uses 6 annual cutoff dates that simulate the generation of forecast once per year over the last 6 years. We'll comsume data up to each cutoff date to fit/train models, and then evaluate over the next 18 months. In this notebook, we're only concerned with producing the retrospective forecasts and we'll do the analysis all together in another notebook.

In [474]:
# report_sim_dates = open("../data/utils/experiment_cutoff_dates.txt", 'r').read().split()
report_sim_dates = open("../../data/utils/experiment_cutoff_dates.txt", 'r').read().split()

report_sim_dates

['2020-03-01',
 '2020-09-27',
 '2021-03-14',
 '2021-09-05',
 '2021-12-12',
 '2022-04-03',
 '2022-07-31']

## AutoGluon Data Format

Instructions to format data properly for AutoGluon are here:
https://auto.gluon.ai/stable/tutorials/timeseries/forecasting-quick-start.html

In [475]:
all_data_df_autogluon = all_data.reset_index().melt(id_vars='index', var_name="item_id", value_name="target").rename({"index": "timestamp"}, axis=1)
all_data_df_autogluon

timestamp                 item_id  target
0     2018-01-07        IS_MENTAL_HEALTH  1367.0
1     2018-01-14        IS_MENTAL_HEALTH  1486.0
2     2018-01-21        IS_MENTAL_HEALTH  1637.0
3     2018-01-28        IS_MENTAL_HEALTH  1740.0
4     2018-02-04        IS_MENTAL_HEALTH  1739.0
...          ...                     ...     ...
50369 2023-05-07  statcan_Transportation     0.0
50370 2023-05-14  statcan_Transportation     0.0
50371 2023-05-21  statcan_Transportation     0.0
50372 2023-05-28  statcan_Transportation     0.0
50373 2023-06-04  statcan_Transportation     0.0

[50374 rows x 3 columns]

In [476]:
pd.options.mode.chained_assignment = None  # Suppress SettingWithCopyWarning

def get_autogluon_df(study_category, cutoff_date):
    global study_df
    global other_categories
    other_categories = [category for category in all_covariates if category != study_category]
    study_df = all_data_df_autogluon.loc[(all_data_df_autogluon.item_id == study_category) & (all_data_df_autogluon.timestamp <= cutoff_date)]
    for category in other_categories:
        study_df.loc[study_df.index, f"exogenous_{category}"] = all_data[category][study_df.timestamp].values
    return study_df

In [477]:
pd.options.mode.chained_assignment = None  # Suppress SettingWithCopyWarning

def get_autogluon_global_df(cutoff_date):

    return all_data_df_autogluon.loc[all_data_df_autogluon.timestamp <= cutoff_date]

In [478]:
pd.options.mode.chained_assignment = None  # Suppress SettingWithCopyWarning

def get_autogluon_global_with_covariates_df(cutoff_date="2023-03-01"):

    all_autogluon_dfs = []
    for category in all_data.columns:
        print(category)
        all_autogluon_dfs.append(get_autogluon_df(category, cutoff_date))
        
    return pd.concat(all_autogluon_dfs, axis=0).dropna(axis=1)

In [479]:
study_df = get_autogluon_df("IS_MENTAL_HEALTH", "2023-03-01")
study_df

/tmp/ipykernel_29817/1138884122.py:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  study_df.loc[study_df.index, f"exogenous_{category}"] = all_data[category][study_df.timestamp].values
/tmp/ipykernel_29817/1138884122.py:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  study_df.loc[study_df.index, f"exogenous_{category}"] = all_data[category][study_df.timestamp].values
/tmp/ipykernel_29817/1138884122.py:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which 

timestamp           item_id  target  exogenous_IS_SUBSTANCE_ABUSE  \
0   2018-01-07  IS_MENTAL_HEALTH  1367.0                         701.0   
1   2018-01-14  IS_MENTAL_HEALTH  1486.0                         832.0   
2   2018-01-21  IS_MENTAL_HEALTH  1637.0                         911.0   
3   2018-01-28  IS_MENTAL_HEALTH  1740.0                         888.0   
4   2018-02-04  IS_MENTAL_HEALTH  1739.0                         892.0   
..         ...               ...     ...                           ...   
264 2023-01-29  IS_MENTAL_HEALTH  1805.0                        1076.0   
265 2023-02-05  IS_MENTAL_HEALTH  2869.0                        1564.0   
266 2023-02-12  IS_MENTAL_HEALTH  2079.0                        1155.0   
267 2023-02-19  IS_MENTAL_HEALTH  2556.0                        1464.0   
268 2023-02-26  IS_MENTAL_HEALTH  2561.0                        1314.0   

     exogenous_IS_PROBLEM_GAMBLING  exogenous_IS_OTHER  \
0                            111.0               243.0   
1                            170.0               218.0   
2                            206.0               206.0   
3                            164.0               158.0   
4                            171.0               144.0   
..                             ...                 ...   
264                          167.0                22.0   
265                          206.0                32.0   
266                          152.0                28.0   
267                          185.0                31.0   
268                          232.0                33.0   

     exogenous_connex_IS_MENTAL_HEALTH_Concurrent Disorder Clients  \
0                                                 69.0               
1                                                 84.0               
2                                                 46.0               
3                                                 86.0               
4                                                 87.0               
..                                                 ...               
264                                                0.0               
265                                                0.0               
266                                                0.0               
267                                                0.0               
268                                                0.0               

     exogenous_connex_IS_SUBSTANCE_ABUSE_Concurrent Disorder Clients  \
0                                                 69.0                 
1                                                 94.0                 
2                                                 47.0                 
3                                                 89.0                 
4                                                 87.0                 
..                                                 ...                 
264                                                0.0                 
265                                                0.0                 
266                                                0.0                 
267                                                0.0                 
268                                                0.0                 

     exogenous_connex_IS_PROBLEM_GAMBLING_Concurrent Disorder Clients  \
0                                                  7.0                  
1                                                  6.0                  
2                                                  4.0                  
3                                                  1.0                  
4                                                 19.0                  
..                                                 ...                  
264                                                0.0                  
265                                                0.0                  
266                                                0.0  

In [480]:
autogluon_global_with_covariates_df = get_autogluon_global_with_covariates_df("2023-03-01")
autogluon_global_with_covariates_df


IS_MENTAL_HEALTH


/tmp/ipykernel_29817/1138884122.py:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  study_df.loc[study_df.index, f"exogenous_{category}"] = all_data[category][study_df.timestamp].values
/tmp/ipykernel_29817/1138884122.py:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  study_df.loc[study_df.index, f"exogenous_{category}"] = all_data[category][study_df.timestamp].values
/tmp/ipykernel_29817/1138884122.py:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which 

IS_SUBSTANCE_ABUSE


/tmp/ipykernel_29817/1138884122.py:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  study_df.loc[study_df.index, f"exogenous_{category}"] = all_data[category][study_df.timestamp].values
/tmp/ipykernel_29817/1138884122.py:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  study_df.loc[study_df.index, f"exogenous_{category}"] = all_data[category][study_df.timestamp].values
/tmp/ipykernel_29817/1138884122.py:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which 

IS_PROBLEM_GAMBLING


...

/tmp/ipykernel_29817/1138884122.py:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  study_df.loc[study_df.index, f"exogenous_{category}"] = all_data[category][study_df.timestamp].values
/tmp/ipykernel_29817/1138884122.py:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  study_df.loc[study_df.index, f"exogenous_{category}"] = all_data[category][study_df.timestamp].values
/tmp/ipykernel_29817/1138884122.py:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which 

statcan_Shelter


/tmp/ipykernel_29817/1138884122.py:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  study_df.loc[study_df.index, f"exogenous_{category}"] = all_data[category][study_df.timestamp].values
/tmp/ipykernel_29817/1138884122.py:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  study_df.loc[study_df.index, f"exogenous_{category}"] = all_data[category][study_df.timestamp].values
/tmp/ipykernel_29817/1138884122.py:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which 

statcan_Transportation


timestamp                 item_id  target
0     2018-01-07        IS_MENTAL_HEALTH  1367.0
1     2018-01-14        IS_MENTAL_HEALTH  1486.0
2     2018-01-21        IS_MENTAL_HEALTH  1637.0
3     2018-01-28        IS_MENTAL_HEALTH  1740.0
4     2018-02-04        IS_MENTAL_HEALTH  1739.0
...          ...                     ...     ...
50355 2023-01-29  statcan_Transportation   164.3
50356 2023-02-05  statcan_Transportation   164.3
50357 2023-02-12  statcan_Transportation   164.3
50358 2023-02-19  statcan_Transportation   164.3
50359 2023-02-26  statcan_Transportation   164.3

[47882 rows x 3 columns]

In [481]:
all_data_df_autogluon

timestamp                 item_id  target
0     2018-01-07        IS_MENTAL_HEALTH  1367.0
1     2018-01-14        IS_MENTAL_HEALTH  1486.0
2     2018-01-21        IS_MENTAL_HEALTH  1637.0
3     2018-01-28        IS_MENTAL_HEALTH  1740.0
4     2018-02-04        IS_MENTAL_HEALTH  1739.0
...          ...                     ...     ...
50369 2023-05-07  statcan_Transportation     0.0
50370 2023-05-14  statcan_Transportation     0.0
50371 2023-05-21  statcan_Transportation     0.0
50372 2023-05-28  statcan_Transportation     0.0
50373 2023-06-04  statcan_Transportation     0.0

[50374 rows x 3 columns]

In [482]:
get_autogluon_global_df("2023-04-30")

timestamp                 item_id  target
0     2018-01-07        IS_MENTAL_HEALTH  1367.0
1     2018-01-14        IS_MENTAL_HEALTH  1486.0
2     2018-01-21        IS_MENTAL_HEALTH  1637.0
3     2018-01-28        IS_MENTAL_HEALTH  1740.0
4     2018-02-04        IS_MENTAL_HEALTH  1739.0
...          ...                     ...     ...
50364 2023-04-02  statcan_Transportation     0.0
50365 2023-04-09  statcan_Transportation     0.0
50366 2023-04-16  statcan_Transportation     0.0
50367 2023-04-23  statcan_Transportation     0.0
50368 2023-04-30  statcan_Transportation     0.0

[49484 rows x 3 columns]

## Plot forecast range with context

We could add different elements to plots including some error analysis, emphasis on different quantiles, etc.

In [483]:
import matplotlib.pyplot as plt
import matplotlib.dates as mdates

def plot_quantile_forecast(category, context_df, forecast_df, actual_df, cutoff_date, save_path=None, show_plots=True, model_name=""):

    fig, ax = plt.subplots(figsize=(10,6))

    # Context
    context_df = pd.concat((context_df, actual_df))
    ax.plot(context_df.index, context_df.values, color='black', label='Ground Truth')

    # Confidence range between 0.01 and 0.99 quantiles
    ax.fill_between(
        forecast_df.index,
        forecast_df[f"q_0.05"],
        forecast_df[f"q_0.95"],
        facecolor='purple',
        alpha=0.5,
        label='95% Confidence'
    )

    # Add a line trace for the median
    ax.plot(forecast_df.index, forecast_df[f"q_0.5"], color='purple', label='Median Forecast')

    # Update the layout as needed
    ax.set_title(f'{category}\nRetrospective Forecast - {cutoff_date} - COVID-19 Wave#{wave_num} \n{model_name}')  

    ax.set_xlabel('Date')
    ax.set_ylabel('Number of Interactions')
    ax.axvline(pd.to_datetime(cutoff_date), label="Cutoff Date", color='black', ls='--', ms=1, alpha=0.5)
    ax.legend()
    ax.xaxis.set_major_locator(mdates.YearLocator())
    ax.xaxis.set_major_formatter(mdates.DateFormatter('%Y'))
    plt.xticks(rotation=45)

    # Show the figure
    plt.grid(axis='y')

    if show_plots:
        plt.show()

    # Save the figure if the path is specified
    if save_path:
        fig.savefig(save_path, dpi=300 if save_path.endswith("png") else None) # High res for png


## Main experiment loop - non-global models

In [484]:
if "global" not in EXP_BASE:
    for model_type in EXP_MODEL_LIST:
        EXPERIMENT_NAME = f"{EXP_BASE}_{model_type}"
        wave_num = 0

        for cutoff_date in report_sim_dates:
            wave_num+=1
            forecast_output_dir = f"./output/experiments/{EXPERIMENT_NAME}/{str(prediction_length)}_weeks/{cutoff_date}/forecasts"
            plot_output_dir = f"./output/experiments/{EXPERIMENT_NAME}/{str(prediction_length)}_weeks/{cutoff_date}/plots"
            training_output_dir = f"./output/experiments/{EXPERIMENT_NAME}/{str(prediction_length)}_weeks/{cutoff_date}/training_results"
            pathlib.Path(forecast_output_dir).mkdir(parents=True, exist_ok=True)
            pathlib.Path(plot_output_dir).mkdir(parents=True, exist_ok=True)
            pathlib.Path(training_output_dir).mkdir(parents=True, exist_ok=True)
            
            aggregated_forecast_df = pd.DataFrame()

           
            for category in target_categories:
                
                for week in range(26):
                    start_date = pd.to_datetime(cutoff_date) + pd.DateOffset(weeks=week) - pd.DateOffset(weeks=prediction_length) 
#                     end_date = start_date + pd.DateOffset(weeks=prediction_length)

                    # Assuming the function 'get_autogluon_global_df' can handle start and end dates
                    train_data = get_autogluon_global_df(start_date) 

                    predictor = TimeSeriesPredictor(
                        prediction_length=prediction_length,
                        path=f"./output/experiments/{EXPERIMENT_NAME}/{str(prediction_length)}_weeks/{cutoff_date}/model_files",
                        target="target",
                        eval_metric="MAPE",
                        quantile_levels=[0.01, 0.05, 0.1, 0.25, 0.75, 0.9, 0.95, 0.99],
                    )

                    if model_type in AVAILABLE_PRESETS:
                        predictor.fit(
                            train_data,
                            presets=model_type,
                            excluded_model_types=["DirectTabular"],
                            time_limit=1800*2,
                        )
                    else:
                        model_params = {}
                        predictor.fit(
                            train_data,
                            hyperparameters={
                                model_type: model_params,
                            },
                            time_limit=1800,
                        )


                        with open(f"{training_output_dir}/{category}.txt", 'w') as f:
                            f.write(str(predictor.fit_summary()))

                        forecast_df = predictor.predict(train_data).loc[category]
                        forecast_df = forecast_df.rename(
                            {"mean": "q_0.5"} | {col: f"q_{col}" for col in forecast_df.columns if col != "mean"},
                            axis=1
                        )

                        # Aggregating forecast data
                        weekly_forecast = forecast_df.iloc[-prediction_length:]  # Taking the last 'prediction_length' entries
                        aggregated_forecast_df = pd.concat([aggregated_forecast_df, pd.DataFrame(weekly_forecast.iloc[-1])], axis=1)

                aggregated_forecast_df = aggregated_forecast_df.T
                context_df = df[category].loc[(df.index >= pd.to_datetime(cutoff_date) - pd.DateOffset(weeks=context_length)) & (df.index <= cutoff_date)]
                actual_df = df[category].loc[(df.index > cutoff_date) & (df.index <= df.index.max())]

                aggregated_forecast_df.to_csv(f"{forecast_output_dir}/{category}.csv")
                plot_quantile_forecast(
                    category=category,          # The target category name
                    context_df=context_df,      # Historical data to plot
                    forecast_df=aggregated_forecast_df,    # Quantile forecast dataframe
                    actual_df=actual_df,        # 'actual' data to plot against forecast
                    save_path=f"{plot_output_dir}/{category}.svg", 
                    cutoff_date=cutoff_date,
                    show_plots=True,
                    model_name=predictor.get_model_best()
                )

# Main experiment loop - global models

In [ ]:
if "global" in EXP_BASE:
    for model_type in EXP_MODEL_LIST:
        EXPERIMENT_NAME = f"{EXP_BASE}_{model_type}"
        wave_num = 0

        for cutoff_date in report_sim_dates:
            wave_num += 1
            forecast_output_dir = f"./output/experiments/{EXPERIMENT_NAME}/{str(prediction_length)}_weeks/{cutoff_date}/forecasts"
            plot_output_dir = f"./output/experiments/{EXPERIMENT_NAME}/{str(prediction_length)}_weeks/{cutoff_date}/plots"
            training_output_dir = f"./output/experiments/{EXPERIMENT_NAME}/{str(prediction_length)}_weeks/{cutoff_date}/training_results"
            pathlib.Path(forecast_output_dir).mkdir(parents=True, exist_ok=True)
            pathlib.Path(plot_output_dir).mkdir(parents=True, exist_ok=True)
            pathlib.Path(training_output_dir).mkdir(parents=True, exist_ok=True)

            if "covariates" in EXP_BASE:
                train_data = get_autogluon_global_with_covariates_df(cutoff_date)
            else:
                train_data = get_autogluon_global_df(cutoff_date)

            aggregated_forecast_df = pd.DataFrame()

           
            for category in target_categories:

                predictor = TimeSeriesPredictor(
                    prediction_length=prediction_length,
                    path=f"./output/experiments/{EXPERIMENT_NAME}/{str(prediction_length)}_weeks/{cutoff_date}/model_files",
                    target="target",
                    eval_metric="MAPE",
                    quantile_levels=[0.01, 0.05, 0.1, 0.25, 0.75, 0.9, 0.95, 0.99],
                )

                if model_type in AVAILABLE_PRESETS:
                    predictor.fit(
                        train_data,
                        presets=model_type,
                        excluded_model_types=["DirectTabular"],
                        time_limit=1800*9,
                    )
                else:
                    model_params = {}
                    predictor.fit(
                        train_data,
                        hyperparameters={
                            model_type: model_params,
                        },
                        time_limit=1800,
                    )


                for week in range(26):
                    start_date = pd.to_datetime(cutoff_date) + pd.DateOffset(weeks=week) - pd.DateOffset(weeks=prediction_length) 
                    end_date = start_date + pd.DateOffset(weeks=prediction_length)

                    # Assuming the function 'get_autogluon_global_df' can handle start and end dates
                    train_data = get_autogluon_global_df(start_date) 


                    with open(f"{training_output_dir}/{category}.txt", 'w') as f:
                        f.write(str(predictor.fit_summary()))

                    forecast_df = predictor.predict(train_data).loc[category]
                    forecast_df = forecast_df.rename(
                        {"mean": "q_0.5"} | {col: f"q_{col}" for col in forecast_df.columns if col != "mean"},
                        axis=1
                    )

                    # Aggregating forecast data
                    weekly_forecast = forecast_df.iloc[-prediction_length:]  # Taking the last 'prediction_length' entries
                    aggregated_forecast_df = pd.concat([aggregated_forecast_df, pd.DataFrame(weekly_forecast.iloc[-1])], axis=1)

                aggregated_forecast_df = aggregated_forecast_df.T
                context_df = df[category].loc[(df.index >= pd.to_datetime(cutoff_date) - pd.DateOffset(weeks=context_length)) & (df.index <= cutoff_date)]
                actual_df = df[category].loc[(df.index > cutoff_date) & (df.index <= df.index.max())]

                aggregated_forecast_df.to_csv(f"{forecast_output_dir}/{category}.csv")
                plot_quantile_forecast(
                    category=category,          # The target category name
                    context_df=context_df,      # Historical data to plot
                    forecast_df=aggregated_forecast_df,    # Quantile forecast dataframe
                    actual_df=actual_df,        # 'actual' data to plot against forecast
                    save_path=f"{plot_output_dir}/{category}.svg", 
                    cutoff_date=cutoff_date,
                    show_plots=True,
                    model_name=predictor.get_model_best()
                )
            # Save the aggregated forecast outside the weekly loop
#             aggregated_forecast_df.to_csv(f"{forecast_output_dir}/aggregated_forecast.csv")

            # Other code for plotting and further analysis...


In [ ]:
predictor.get_model_best()

In [ ]:
predictor.fit_summary()

In [ ]:
train_data